In [ ]:
# %pip install PySuperTuxKart==1.1.2
# # !pip install imageio==2.4.1
# !pip install imageio

^C
ERROR: Operation cancelled by user
Note: you may need to restart the kernel to use updated packages.


# Setup

In [ ]:
import os
os._exit(00)

In [ ]:
# Environmental flag to visualize in colab.


%env ON_COLAB=1
from importlib import reload
import numpy as np
import torch

from modules_official import dense_transforms;reload(dense_transforms)
from modules_official import controller;reload(controller)
from modules_official import planner;reload(planner)
from modules_official import train;reload(train)
from modules_official import util;reload(util)


from modules_jt import control_func_module_jt;reload(control_func_module_jt)
from modules_jt import generate_dataset_module_jt;reload(generate_dataset_module_jt)
from modules_jt import train_module_jt;reload(train_module_jt)
from modules_jt import train_module_jt2;reload(train_module_jt2)


from modules_team import control_func_module_team



if 'pytux_jt' not in locals():
    pytux_jt = util.PyTuxJT()



env: ON_COLAB=1





# JT 1

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive/', force_remount=True)

# %cd /content/drive/MyDrive/supertuxkart_data/
# !ls
# !pwd

# %cd /content

Mounted at /content/drive/


##### PlannerResJT

In [ ]:
from torch.nn import *
import torch.nn.functional as F

class PlannerResJT(torch.nn.Module):
  def __init__(self):

    super().__init__()
    self.batch_norm=BatchNorm2d(num_features=3)
    self.resnet=torch.hub.load('pytorch/vision:v0.10.0', 'resnet50', pretrained=False)
    

  def forward(self, image_batch):# [batch_size,channel_size=3,height=96,width=128]
    """
    Your code here
    Predict the aim point in image coordinate, given the supertuxkart image
    @img: (B,3,96,128)
    return (B,2) 
    """
    
    x = self.batch_norm(image_batch)
    x = self.resnet(x)#[batch_size, 1, 6, 8]
    x=x.reshape(-1,25,40)
    # print(x.shape)

    return spatial_argmax_jt(x) #輸入是[batch_size,height=6,width=8],輸出是[batch_size,2]


def spatial_argmax_jt(logit):
    """
    Compute the soft-argmax of a heatmap
    :param logit: A tensor of size BS x H x W
    :return: A tensor of size BS x 2 the soft-argmax in normalized coordinates (-1 .. 1)
    """
   
   
    weights = F.softmax(logit.view(logit.size(0), -1), dim=-1).view_as(logit)
    #ok, let's discuss what this just did
    # logit.view(logit.size(0), -1) reshapes the input, which is a 1xaxb tensor as 
    # 1 x ab
    #softmax then takes the softmax
    #finally, this is converted back to a 1xaxb tensor

    #the following code computes the center of mass
    #formula in more convenient form is given in slides
    # print(weights[0])
    # linspace(-1,1)是一個數列，第一個點為-1，最後一個點為 1，一共有 logit.shape[2]個數。類似於找重心。
    firstcoord = (weights.sum(1) * torch.linspace(-1, 1, logit.size(2)).to(logit.device)[None]).sum(1)
    secondcoord = (weights.sum(2) * torch.linspace(-1, 1, logit.size(1)).to(logit.device)[None]).sum(1)
    a = torch.stack((firstcoord, secondcoord), 1)

    return a


##### train model

In [ ]:
%reload_ext tensorboard
%tensorboard --logdir /home/phuang/kart/dev2/train_log --reload_interval 1

In [ ]:
args_jt=train_module_jt2.TrainArgsJT2()
args_jt.num_workers=2
args_jt.random_seed=99998
args_jt.val_interval=1
tracks = [
    'lighthouse', 
    'zengarden', 
    'hacienda', 
    'snowtuxpeak',
    'cornfield_crossing',
    'scotland',
    'cocoa_temple'
          ]
args_jt.tracks=tracks

args_jt.trainset_dirs=[
    'trainset_5000_samjt',
    'trainset_5000_charlie',
    # 'trainset_5000_jt'
          ]
args_jt.valset_dirs=[
    'valset_5000_samjt',
    'valset_5000_charlie',
    # 'valset_5000_jt'
          ]

args_jt.learning_rate=1e-3
args_jt.num_epochs=0
args_jt.proportion=1

args_jt.planner_name="planner_res_jt_v2.th";
args_jt.planner_type=PlannerResJT

train_module_jt2.train_jt2(args_jt)


Initializing Model =================================


Using cache found in /home/phuang/.cache/torch/hub/pytorch_vision_v0.10.0


PlannerResJT(
  (batch_norm): BatchNorm2d(3, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (resnet): ResNet(
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): Bottleneck(
        (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_

KeyboardInterrupt: ignored

##### test model 

In [ ]:

def test_planner_jt(pytux,tracks, planner_name,planner_type, control_func,verbose):
    # Load model
    planner = train_module_jt.load_planner_jt(planner_name,planner_type).eval()
    print(planner)
    planner.to("cpu")

    sum=0
    for t in tracks:
        steps, how_far = pytux.rollout(t, control_func, planner=planner, max_frames=1000, verbose=verbose)
        sum=sum+steps
        print(t,steps, how_far)
    print("total",sum)

In [ ]:
tracks = [
    'lighthouse', 
    'zengarden', 
    'hacienda', 
    'snowtuxpeak',
    'cornfield_crossing',
    'scotland',
    'cocoa_temple'
          ]   

test_planner_jt(pytux_jt,
                tracks,
                planner_name="planner_res_jt_v1.th",
                planner_type=PlannerResJT,
                control_func=control_func_module_team.control_func_charlie,
                verbose=True)


Using cache found in /home/phuang/.cache/torch/hub/pytorch_vision_v0.10.0


PlannerResJT(
  (batch_norm): BatchNorm2d(3, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (resnet): ResNet(
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): Bottleneck(
        (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_

Moviepy - Done !
Moviepy - video ready __temp__.mp4


lighthouse 478 1.0001619777630546
Finished at t=404
Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


...

cornfield_crossing 670 0.9980587963146299
Finished at t=561
Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


scotland 561 0.9980099966888403
Finished at t=640
Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


cocoa_temple 640 0.9990938786100811
total 3804


3725
3829

t=386 zengarden
t=415 lighthouse
t=541 hacienda
t=586 snowtuxpeak
t=691 cornfield_crossing
t=613 scotland 
t=775 cocoa_temple

##### val_planner_jt

In [ ]:
class ValArgsJT:
  def __init__(self):
    self.num_workers=2
    self.transform='Compose([ToTensor()])'
    

def val_planner_jt(args:ValArgsJT):


  print("Initializing Model =================================")
  model = args.planner_type()
  print(model)
  train_logger, valid_logger = None, None


  print("installing torch ...")

  device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

  model = model.to(device)
  model.load_state_dict(torch.load(path.join(path.dirname(FILE_PATH), args.planner_name)))

  loss = torch.nn.L1Loss()
  
  print("installing inspect ...")
  
  transform = eval(args.transform, {k: v for k, v in inspect.getmembers(dense_transforms) if inspect.isclass(v)})
  print("loading data ...")
  val_data = load_data_jt(args.valset_dirs, tracks=args.tracks,transform=transform, num_workers=args.num_workers)

  global_step = 0
  print("Begin =================================")
  with torch.no_grad():
    for epoch in range(1):
        model.eval()
        losses = []
        for img, label in val_data:
            img, label = img.to(device), label.to(device)

            pred = model(img)
            loss_val = loss(pred, label)

            if train_logger is not None:
                train_logger.add_scalar('loss', loss_val, global_step)
                if global_step % 100 == 0:
                    log(train_logger, img, label, pred, global_step)

            global_step += 1
            losses.append(loss_val.detach().cpu().numpy())
        
        avg_loss = np.mean(losses)

        print('loss = %0.3f' % (avg_loss))


In [ ]:
tracks = [
    'lighthouse', 
    'zengarden', 
    'hacienda', 
    'snowtuxpeak',
    'cornfield_crossing',
    'scotland',
    # 'cocoa_temple'
          ]
args_jt=ValArgsJT()
args_jt.valset_dirs=[
    'mini_valset'
          ]  
args_jt.tracks=tracks

args_jt.planner_name="planner_jt_l1.th"
layer_list_g=l1
args_jt.planner_type=PlannerJT

val_planner_jt(args_jt)

Initializing Model =================================
PlannerJT(
  (layers): Sequential(
    (0): Conv2d(3, 16, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (1): ReLU(inplace=True)
    (2): Conv2d(16, 32, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (3): ReLU(inplace=True)
    (4): Conv2d(32, 32, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (5): ReLU(inplace=True)
    (6): Conv2d(32, 32, kernel_size=(5, 5), stride=(2, 2), padding=(2, 2))
    (7): ReLU(inplace=True)
    (8): Conv2d(32, 1, kernel_size=(1, 1), stride=(1, 1))
  )
)
installing torch ...
installing inspect ...
loading data ...
Begin =================================
loss = 0.053


##### get_demo_images_batch

In [ ]:
def get_demo_images_batch():

    dataset_path="dataset_base/trainset_5000_samjt/lighthouse"
    transform=dense_transforms.ToTensor()

    data = []
    NUM=7
    counter=NUM
    from PIL import Image
    from glob import glob
    from os import path

    for f in glob(path.join(dataset_path, '*.csv')):

      i = Image.open(f.replace('.csv', '.png'))
      i.load()
      data.append((i, np.loadtxt(f, dtype=np.float32, delimiter=',')))

      counter-=1
      if counter==0:
        break


    image_list=[]
    for idx in range(NUM):
      sample = data[idx]
      sample = transform(*sample)
      image, label = sample
      image_list.append(image)

    image_batch=torch.stack(image_list)
    return image_batch

demo_batch=get_demo_images_batch()
print(demo_batch.shape)

torch.Size([7, 3, 96, 128])


# JT 2

In [ ]:
# planner_jt=load_planner_jt(planner_name="planner_jt.th",planner_type=PlannerJT,)
# layer_list_g=ll4
planner_jt=PlannerResJT()
planner_jt.eval()
print(planner_jt)
planner_jt(demo_batch)





Using cache found in /home/phuang/.cache/torch/hub/pytorch_vision_v0.10.0
/usr/local/anaconda3/lib/python3.8/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/anaconda3/lib/python3.8/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=None`.
  warnings.warn(msg)


PlannerResJT(
  (batch_norm): BatchNorm2d(3, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (resnet): ResNet(
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): Bottleneck(
        (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_

tensor([[-0.0482,  0.0552],
        [-0.0947,  0.0845],
        [-0.0882,  0.0996],
        [-0.0856,  0.0901],
        [-0.0693,  0.0706],
        [-0.1533,  0.1565],
        [-0.0560,  0.0460]], grad_fn=<StackBackward0>)

# Track Point

In [ ]:
# print(util.distance_g2)
print(util.track_g.path_distance)
print(util.track_g.path_nodes.shape)
# print(util.distance_g2%util.track_g.path_distance[-1, 1])

# print(len(util.track_g.path_nodes))
print(util.track_g.path_distance.shape)
# for i in range(util.track_g.path_distance.shape[0]-1):
print(util.track_g.path_distance[221])


[[   0.          3.982571]
 [   3.982571    8.023966]
 [   8.023966   12.083368]
 [  12.083368   16.117512]
 [  16.117512   20.08325 ]
 [  20.08325    23.938736]
 [  23.938736   27.646555]
 [  27.646555   31.17108 ]
 [  31.17108    34.486576]
 [  34.486576   37.57803 ]
 [  37.57803    40.672424]
 [  40.672424   44.001328]
 [  44.001328   47.553654]
 [  47.553654   51.301464]
 [  51.301464   55.208412]
 [  55.208412   59.235023]
 [  59.235023   63.34548 ]
 [  63.34548    67.50709 ]
 [  67.50709    71.69942 ]
 [  71.69942    75.91751 ]
 [  75.91751    80.172356]
 [  80.172356   84.50309 ]
 [  84.50309    88.97189 ]
 [  88.97189    93.669334]
 [  93.669334   98.70666 ]
 [  98.70666   104.2074  ]
 [ 104.2074    109.777985]
 [ 109.777985  115.10927 ]
 [ 115.10927   120.38672 ]
 [ 120.38672   125.71437 ]
 [ 125.71437   131.12929 ]
 [ 131.12929   136.6226  ]
 [ 136.6226    142.16223 ]
 [ 142.16223   147.71236 ]
 [ 147.71236   153.25061 ]
 [ 153.25061   158.78877 ]
 [ 158.78877   164.38953 ]
 